In [3]:
from datetime import date
import numpy as np
import pandas as pd
import datetime
import sys
from yahoo_finance_api2 import share
from yahoo_finance_api2.exceptions import YahooFinanceError

In [8]:
import plotly
plotly.__version__

from datetime import date

In [9]:
import cufflinks as cf
import plotly.offline
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

In [10]:
# (*) Graph objects to piece together plots
import plotly.graph_objs as go

In [11]:
def fetch_data(ticker_list, verbose=True):
    stock_list = []
    for tick in ticker_list:
        if verbose:
            print(f"Fetching ticker: {tick}...")
        my_share = None
        my_share = share.Share(tick)
        symbol_data = None
        try:
            symbol_data = my_share.get_historical(share.PERIOD_TYPE_YEAR,7,
                                                  share.FREQUENCY_TYPE_DAY,1)
        except YahooFinanceError as e:
            print(e.message)
            sys.exit(1)

        stock_list.append(symbol_data)
        if verbose:
            print(f"Len of timestamp series: {len(symbol_data['timestamp'])}")
    return stock_list

def datetime_from_timestamp(timestamp):
    x = datetime.date.fromtimestamp(int(str(timestamp)[:-3]))
    return pd.to_datetime(
        f"{str(x.year)}-{str(x.month)}-{str(x.day)}")

In [12]:
ticker_list=['BARN.SW',
             'E5H.SI',
             'BN.VI', # DANONE
             'UN', # unilever
             'LISN.SW', #lind
             'SJM', #JM SMUCKER 
             'MDLZ', # mondelez
             'HRL', # Hormel foods
             'GIS', # GENERAL MILLS
             'HSY',
             'KIKOY',
             'WHG',
             'ADM',
             'K',
             'NESN.SW',
             'TATE.L',
             'BG',
             'ABF.L',
             'CAG'
             ]

data = fetch_data(ticker_list)

Fetching ticker: BARN.SW...
Len of timestamp series: 1753
Fetching ticker: E5H.SI...
Len of timestamp series: 1757
Fetching ticker: BN.VI...
Len of timestamp series: 1741
Fetching ticker: UN...
Len of timestamp series: 1762
Fetching ticker: LISN.SW...
Len of timestamp series: 1753
Fetching ticker: SJM...
Len of timestamp series: 1762
Fetching ticker: MDLZ...
Len of timestamp series: 1762
Fetching ticker: HRL...
Len of timestamp series: 1762
Fetching ticker: GIS...
Len of timestamp series: 1762
Fetching ticker: HSY...
Len of timestamp series: 1762
Fetching ticker: KIKOY...
Len of timestamp series: 1761
Fetching ticker: WHG...
Len of timestamp series: 1762
Fetching ticker: ADM...
Len of timestamp series: 1762
Fetching ticker: K...
Len of timestamp series: 1762
Fetching ticker: NESN.SW...
Len of timestamp series: 1753
Fetching ticker: TATE.L...
Len of timestamp series: 1770
Fetching ticker: BG...
Len of timestamp series: 1762
Fetching ticker: ABF.L...
Len of timestamp series: 1770
Fetchin

In [13]:
def get_pandas_df(data):
    min_series = []
    # Take the first as base df
    stocks = pd.DataFrame()
    stocks['timestamp'] = list(map(datetime_from_timestamp, data[0]['timestamp']))
    stocks[f'{ticker_list[0]}_close'] = data[0]['close']
    for idx, stock in enumerate(data):
        if idx!=0:
            temp_df = pd.DataFrame()
            temp_df['timestamp'] = list(map(datetime_from_timestamp, stock['timestamp']))
            temp_df[f'{ticker_list[idx]}_close'] = stock['close']
            stocks = stocks.merge(temp_df, how='left', on='timestamp')
    stocks = stocks.fillna(method='ffill')
    stocks = stocks.fillna(method='backfill')
    return stocks

In [14]:
stocks_df = get_pandas_df(data)

In [15]:
stocks_df

timestamp  BARN.SW_close  E5H.SI_close  BN.VI_close   UN_close  \
0    2013-11-22         1018.0         0.575    38.892700  38.900002   
1    2013-11-25         1021.0         0.575    38.892700  39.340000   
2    2013-11-26         1028.0         0.585    38.892700  39.060001   
3    2013-11-27         1025.0         0.575    38.892700  39.090000   
4    2013-11-28         1031.0         0.575    38.892700  39.090000   
...         ...            ...           ...          ...        ...   
1748 2020-11-16         2026.0         0.146    54.700001  60.750000   
1749 2020-11-17         2000.0         0.153    54.419998  59.930000   
1750 2020-11-18         2016.0         0.152    54.619999  59.230000   
1751 2020-11-19         1988.0         0.148    52.880001  58.980000   
1752 2020-11-20         2022.0         0.150    52.540001  58.705002   

      LISN.SW_close   SJM_close  MDLZ_close  HRL_close  GIS_close   HSY_close  \
0           45850.0  103.949997   33.889999  21.450001  50.119999   96.290001   
1           45805.0  104.309998   33.610001  21.219999  49.880001   95.989998   
2           46300.0  105.620003   33.889999  22.475000  50.480000   96.919998   
3           46385.0  105.610001   33.980000  22.514999  50.529999   97.720001   
4           46695.0  105.610001   33.980000  22.514999  50.529999   97.720001   
...             ...         ...         ...        ...        ...         ...   
1748        84400.0  120.110001   58.680000  52.509998  61.209999  155.119995   
1749        83400.0  118.430000   58.540001  51.330002  61.279999  152.929993   
1750        85000.0  115.769997   57.759998  50.009998  61.130001  150.639999   
1751        84000.0  117.050003   57.599998  49.990002  62.000000  149.399994   
1752        84400.0  114.940002   57.169998  49.570000  61.029999  147.505005   

      KIKOY_close  WHG_close  ADM_close    K_close  NESN.SW_close  \
0         10.0567  56.820000  41.860001  62.470001      66.800003   
1         10.0567  56.750000  41.349998  62.130001      67.300003   
2         10.0567  56.880001  41.599998  61.730000      66.250000   
3         10.0567  57.000000  41.490002  60.880001      66.150002   
4         10.0567  57.000000  41.490002  60.880001      66.199997   
...           ...        ...        ...        ...            ...   
1748      24.7500  11.950000  50.410000  66.580002     105.080002   
1749      24.7500  12.650000  50.160000  66.320000     105.519997   
1750      24.7500  12.420000  49.270000  65.019997     104.959999   
1751      24.7500  12.400000  48.919998  65.209999     104.120003   
1752      24.7500  12.350000  48.665001  64.639999     103.680000   

      TATE.L_close   BG_close  ABF.L_close  CAG_close  
0       794.000000  80.720001       2291.0  25.431906  
1       798.500000  80.349998       2290.0  25.385214  
2       790.500000  80.650002       2250.0  25.252918  
3       787.000000  80.529999       2292.0  25.533073  
4       781.000000  80.529999       2290.0  25.533073  
...            ...        ...          ...        ...  
1748    678.200012  60.689999       2058.0  36.540001  
1749    673.400024  59.380001       2036.0  35.740002  
1750    674.000000  58.380001       2033.0  35.480000  
1751    645.599976  58.529999       1999.5  36.189999  
1752    646.000000  58.360001       1980.0  35.790001  

[1753 rows x 20 columns]

In [17]:
adj_closes = stocks_df[[x for x in stocks_df.columns if x !='timestamp']]

In [18]:
(adj_closes/adj_closes.iloc[0]*100).iplot()

In [19]:
# Mean daily return
returns = np.log(adj_closes/adj_closes.shift(1))
returns.mean()

BARN.SW_close    0.000392
E5H.SI_close    -0.000767
BN.VI_close      0.000172
UN_close         0.000235
LISN.SW_close    0.000348
SJM_close        0.000057
MDLZ_close       0.000298
HRL_close        0.000478
GIS_close        0.000112
HSY_close        0.000243
KIKOY_close      0.000514
WHG_close       -0.000871
ADM_close        0.000086
K_close          0.000019
NESN.SW_close    0.000251
TATE.L_close    -0.000118
BG_close        -0.000185
ABF.L_close     -0.000083
CAG_close        0.000195
dtype: float64

In [20]:
# Annual Returns
returns.mean() * 252

BARN.SW_close    0.098707
E5H.SI_close    -0.193277
BN.VI_close      0.043261
UN_close         0.059193
LISN.SW_close    0.087767
SJM_close        0.014456
MDLZ_close       0.075213
HRL_close        0.120486
GIS_close        0.028328
HSY_close        0.061346
KIKOY_close      0.129536
WHG_close       -0.219527
ADM_close        0.021666
K_close          0.004912
NESN.SW_close    0.063231
TATE.L_close    -0.029671
BG_close        -0.046654
ABF.L_close     -0.020984
CAG_close        0.049143
dtype: float64

In [21]:
# Annual covariance
returns.cov() * 252

BARN.SW_close  E5H.SI_close  BN.VI_close  UN_close  \
BARN.SW_close       0.042928      0.002783     0.007235  0.012799   
E5H.SI_close        0.002783      0.120110     0.001712  0.006402   
BN.VI_close         0.007235      0.001712     0.068796  0.010025   
UN_close            0.012799      0.006402     0.010025  0.044620   
LISN.SW_close       0.014738      0.003525     0.006689  0.013063   
SJM_close           0.007391      0.003078     0.006873  0.014553   
MDLZ_close          0.011227      0.005797     0.007841  0.022967   
HRL_close           0.006894      0.001081     0.005711  0.017296   
GIS_close           0.007590      0.003726     0.005604  0.015672   
HSY_close           0.008149      0.000342     0.006682  0.020345   
KIKOY_close         0.004027      0.008693     0.002469  0.006296   
WHG_close           0.009291      0.008404     0.007849  0.020731   
ADM_close           0.011029      0.009241     0.008405  0.021525   
K_close             0.006484      0.002710     0.005578  0.016291   
NESN.SW_close       0.015338      0.005704     0.009097  0.016178   
TATE.L_close        0.012938      0.008716     0.009123  0.015245   
BG_close            0.010484      0.007801     0.005956  0.019821   
ABF.L_close         0.016396      0.011330     0.011212  0.017861   
CAG_close           0.009066      0.002678     0.005833  0.015947   

               LISN.SW_close  SJM_close  MDLZ_close  HRL_close  GIS_close  \
BARN.SW_close       0.014738   0.007391    0.011227   0.006894   0.007590   
E5H.SI_close        0.003525   0.003078    0.005797   0.001081   0.003726   
BN.VI_close         0.006689   0.006873    0.007841   0.005711   0.005604   
UN_close            0.013063   0.014553    0.022967   0.017296   0.015672   
LISN.SW_close       0.033625   0.005358    0.011624   0.006004   0.006670   
SJM_close           0.005358   0.051572    0.024733   0.023740   0.029880   
MDLZ_close          0.011624   0.024733    0.050299   0.024647   0.026883   
HRL_close           0.006004   0.023740    0.024647   0.046050   0.025304   
GIS_close           0.006670   0.029880    0.026883   0.025304   0.044408   
HSY_close           0.010139   0.022924    0.029168   0.023860   0.025199   
KIKOY_close         0.007015   0.004309    0.010783   0.004836   0.005639   
WHG_close           0.019398   0.009305    0.030555   0.015688   0.015799   
ADM_close           0.011250   0.019135    0.030485   0.019585   0.020417   
K_close             0.004784   0.027066    0.026285   0.023888   0.031225   
NESN.SW_close       0.013690   0.008719    0.011308   0.007838   0.008475   
TATE.L_close        0.012916   0.008110    0.012162   0.007639   0.007529   
BG_close            0.012505   0.013473    0.024325   0.012859   0.014112   
ABF.L_close         0.017688   0.006573    0.013875   0.004252   0.007553   
CAG_close           0.006331   0.026105    0.025489   0.022749   0.026973   

               HSY_close  KIKOY_close  WHG_close  ADM_close   K_close  \
BARN.SW_close   0.008149     0.004027   0.009291   0.011029  0.006484   
E5H.SI_close    0.000342     0.008693   0.008404   0.009241  0.002710   
BN.VI_close     0.006682     0.002469   0.007849   0.008405  0.005578   
UN_close        0.020345     0.006296   0.020731   0.021525  0.016291   
LISN.SW_close   0.010139     0.007015   0.019398   0.011250  0.004784   
SJM_close       0.022924     0.004309   0.009305   0.019135  0.027066   
MDLZ_close      0.029168     0.010783   0.030555   0.030485  0.026285   
HRL_close       0.023860     0.004836   0.015688   0.019585  0.023888   
GIS_close       0.025199     0.005639   0.015799   0.020417  0.031225   
HSY_close       0.051476     0.008983   0.035427   0.023607  0.023302   
KIKOY_close     0.008983     0.118612   0.017798   0.007767  0.004540   
WHG_close       0.035427     0.017798   0.192618   0.041180  0.011927   
ADM_close       0.023607     0.007767   0.041180   0.064854  0.021720   
K_close         0.023302     0.004540   0.011927   0.021720  0.046101  

In [22]:
returns.corr().iplot(kind='heatmap',colorscale="Blues", title="Stocks Correlation Matrix")

In [23]:
num_assets = len(returns.columns)
weights = np.random.dirichlet(np.ones(num_assets), size=1)
weights = weights[0]
print(weights)
print(f"Number of weights: {len(weights)}")
print(f"Sum of weights: {np.sum(weights)}")

[0.00416138 0.09804059 0.13857317 0.01058931 0.00250219 0.04315632
 0.04921141 0.01910155 0.09910313 0.04397046 0.0319958  0.02828914
 0.09295228 0.10600689 0.03694854 0.05996502 0.00427884 0.07468285
 0.05647115]
Number of weights: 19
Sum of weights: 1.0000000000000002


In [24]:
# EXPECTED PORTFOLIO RETURN:
exp_port_return = np.sum(returns.mean()*weights)*252
print(exp_port_return)

0.0024688570815984867


In [25]:
# VARAICNE AND VOLATILITY
port_var = np.dot(weights.T, np.dot(returns.cov()*252, weights))
port_vol = np.sqrt(port_var)
print(port_var)
print(port_vol)

0.01735765786634993
0.13174846437947552


In [26]:
import time

import plotly.graph_objects as go
import numpy as np

def portfolio_simulation(assets, iterations):
    '''
    Runs a simulation by randomly selecting portfolio weights a specified
    number of times (iterations), returns the list of results and plots 
    all the portfolios as well.
    
    Parameters:
    -----------  
        assets: list
            all the assets that are to be pulled from Quandl to comprise
            our portfolio.    
        iterations: int 
            the number of randomly generated portfolios to build.
    
    Returns:
    --------
        port_returns: array
            array of all the simulated portfolio returns.
        port_vols: array
            array of all the simulated portfolio volatilities.
    '''
    
    start = time.time()
    num_assets = len(assets)
    
    # Fetch data 
    data = fetch_data(ticker_list, verbose=False)
    stocks = get_pandas_df(data)
    adj_closes = stocks_df[[x for x in stocks.columns if x !='timestamp']]

    returns = np.log(adj_closes / adj_closes.shift(1))
    
    port_returns = []
    port_vols = []
    
    for i in range (iterations):
        weights = np.random.dirichlet(np.ones(num_assets),size=1)
        weights = weights[0]
        port_returns.append(np.sum(returns.mean() * weights) * 252)
        port_vols.append(np.sqrt(np.dot(weights.T, np.dot(returns.cov() * 252, weights))))
    
    # Convert lists to arrays
    port_returns = np.array(port_returns)
    port_vols = np.array(port_vols)
    len_ret = port_returns.shape[0]
    portfolio_stats = pd.DataFrame()
    portfolio_stats['returns'] = port_returns
    portfolio_stats['vol'] = port_vols
    portfolio_stats = portfolio_stats.sort_values(by='returns', ascending=False)
    portfolio_stats = portfolio_stats.loc[portfolio_stats.returns>=0]
    portfolio_stats = portfolio_stats.iloc[list(range(0,portfolio_stats.shape[0],5)),:]
    
    fig = go.Figure(data=go.Scatter(x=portfolio_stats.vol,
                                    y=portfolio_stats.returns, mode='markers',
                                   marker=dict(
        size=5,
        color=(port_returns / port_vols), #set color equal to a variable
        colorscale='Viridis', # one of plotly colorscales
        showscale=True)))

    fig.show()
    
    print('Elapsed Time: %.2f seconds' % (time.time() - start))
    
    return port_returns, port_vols

In [27]:
port_returns, port_vols = portfolio_simulation(ticker_list, 30000)

Elapsed Time: 65.99 seconds


In [28]:
data = fetch_data(ticker_list, verbose=False)
stocks = get_pandas_df(data)
adj_closes = stocks_df[[x for x in stocks.columns if x !='timestamp']]
returns = np.log(adj_closes / adj_closes.shift(1))

def portfolio_stats(weights):
    # Convert to array in case list was passed instead.
    weights = np.array(weights)
    
    port_return = np.sum(returns.mean() * weights) * 252
    port_vol = np.sqrt(np.dot(weights.T, np.dot(returns.cov() * 252, weights)))
    sharpe = port_return/port_vol

    return {'return': port_return, 'volatility': port_vol, 'sharpe': sharpe}

def minimize_sharpe(weights):  
    return -portfolio_stats(weights)['sharpe'] 

def minimize_volatility(weights):  
    # Note that we don't return the negative of volatility here because we 
    # want the absolute value of volatility to shrink, unlike sharpe.
    return portfolio_stats(weights)['volatility'] 

def minimize_return(weights): 
    return -portfolio_stats(weights)['return']

In [29]:
constraints = ({'type' : 'eq', 'fun': lambda x: np.sum(x) -1})
bounds = tuple((0,1) for x in range(num_assets))
initializer = num_assets * [1./num_assets,]

## Efficient frontier - optimal sharpe ration

In [30]:
import scipy.optimize as optimize
optimal_sharpe = optimize.minimize(minimize_sharpe,
                                  initializer,
                                  method = 'SLSQP',
                                  bounds = bounds,
                                  constraints = constraints)
print(optimal_sharpe)

     fun: -0.7961669251306998
     jac: array([-1.02676451e-04,  1.57745986e+00, -1.24774873e-04,  1.51645213e-01,
        8.96155834e-05,  4.33050305e-01,  1.43919952e-01,  1.27136707e-04,
        3.77780467e-01,  1.74795330e-01, -2.74524093e-04,  2.30205638e+00,
        4.37349014e-01,  4.91211496e-01,  1.80201977e-03,  6.81141131e-01,
        8.45722161e-01,  6.58858106e-01,  2.15320364e-01])
 message: 'Optimization terminated successfully'
    nfev: 180
     nit: 9
    njev: 9
  status: 0
 success: True
       x: array([2.30549792e-01, 0.00000000e+00, 2.35634601e-02, 0.00000000e+00,
       2.40718700e-01, 0.00000000e+00, 0.00000000e+00, 3.57839094e-01,
       3.48299948e-18, 1.70775395e-16, 1.47328953e-01, 5.09900282e-16,
       1.03527755e-16, 0.00000000e+00, 0.00000000e+00, 1.50012923e-16,
       1.90467217e-16, 1.13841228e-16, 5.30988014e-17])


In [31]:
optimal_sharpe_weights=optimal_sharpe['x'].round(4)
list(zip(ticker_list,list(optimal_sharpe_weights)))

[('BARN.SW', 0.2305),
 ('E5H.SI', 0.0),
 ('BN.VI', 0.0236),
 ('UN', 0.0),
 ('LISN.SW', 0.2407),
 ('SJM', 0.0),
 ('MDLZ', 0.0),
 ('HRL', 0.3578),
 ('GIS', 0.0),
 ('HSY', 0.0),
 ('KIKOY', 0.1473),
 ('WHG', 0.0),
 ('ADM', 0.0),
 ('K', 0.0),
 ('NESN.SW', 0.0),
 ('TATE.L', 0.0),
 ('BG', 0.0),
 ('ABF.L', 0.0),
 ('CAG', 0.0)]

## Efficient frontier - optimal variance

In [32]:
optimal_variance=optimize.minimize(minimize_volatility,
                                   initializer,
                                   method = 'SLSQP',
                                   bounds = bounds,
                                   constraints = constraints)

print(optimal_variance)
optimal_variance_weights=optimal_variance['x'].round(4)
list(zip(ticker_list,list(optimal_variance_weights)))

     fun: 0.11333361890069292
     jac: array([0.11308568, 0.11324386, 0.11376582, 0.11935735, 0.1133753 ,
       0.11327983, 0.12942318, 0.11332269, 0.11341157, 0.11322567,
       0.11326629, 0.12101564, 0.120868  , 0.11328836, 0.11323321,
       0.11355869, 0.1132541 , 0.11339269, 0.11341744])
 message: 'Optimization terminated successfully'
    nfev: 220
     nit: 11
    njev: 11
  status: 0
 success: True
       x: array([8.99228108e-02, 7.64018533e-02, 1.04371918e-01, 0.00000000e+00,
       1.56704015e-01, 4.35178118e-02, 0.00000000e+00, 8.80819054e-02,
       1.63229488e-02, 1.82621196e-02, 6.27108534e-02, 2.16840434e-18,
       0.00000000e+00, 8.69763934e-02, 1.82807585e-01, 3.97580430e-02,
       2.31469068e-02, 5.69206141e-19, 1.10148360e-02])


[('BARN.SW', 0.0899),
 ('E5H.SI', 0.0764),
 ('BN.VI', 0.1044),
 ('UN', 0.0),
 ('LISN.SW', 0.1567),
 ('SJM', 0.0435),
 ('MDLZ', 0.0),
 ('HRL', 0.0881),
 ('GIS', 0.0163),
 ('HSY', 0.0183),
 ('KIKOY', 0.0627),
 ('WHG', 0.0),
 ('ADM', 0.0),
 ('K', 0.087),
 ('NESN.SW', 0.1828),
 ('TATE.L', 0.0398),
 ('BG', 0.0231),
 ('ABF.L', 0.0),
 ('CAG', 0.011)]

In [33]:
# Make an array of 50 returns betweeb the minimum return and maximum return
# discovered earlier.
target_returns = np.linspace(0,0.12,100)

# Initialize optimization parameters
minimal_volatilities = []
bounds = tuple((0,1) for x in weights)
initializer = num_assets * [1./num_assets,]

for target_return in target_returns:
    
    constraints = ({'type':'eq','fun': lambda x: portfolio_stats(x)['return']-target_return},
                   {'type':'eq','fun': lambda x: np.sum(x)-1})
       
    optimal = optimize.minimize(minimize_volatility,
                              initializer,
                              method = 'SLSQP',
                              bounds = bounds,

                                constraints = constraints)
    
    minimal_volatilities.append(optimal['fun'])

minimal_volatilities = np.array(minimal_volatilities)

In [36]:
port_returns = np.array(port_returns)
port_vols = np.array(port_vols)
len_ret = port_returns.shape[0]
portfolio_stats1 = pd.DataFrame()
portfolio_stats1['returns'] = port_returns
portfolio_stats1['vol'] = port_vols
portfolio_stats1 = portfolio_stats1.sort_values(by='returns', ascending=False)
portfolio_stats1 = portfolio_stats1.loc[portfolio_stats1.returns>=0]
portfolio_stats1 = portfolio_stats1.iloc[list(range(0,portfolio_stats1.shape[0],5)),:]

fig = go.Figure()
fig.add_trace(go.Scatter(x=portfolio_stats1.vol,
                         y=portfolio_stats1.returns, mode='markers',
                         marker=dict(
        size=5,
        color=(port_returns / port_vols), #set color equal to a variable
        colorscale='Viridis', # one of plotly colorscales
        showscale=False)))

fig.add_trace(go.Scatter(x=minimal_volatilities, y=target_returns, mode='markers',
                                   marker=dict(
        size=5,
        symbol='diamond',
        color=(port_returns / port_vols), #set color equal to a variable
        colorscale='Viridis', # one of plotly colorscales
        showscale=True)))

fig.add_trace(go.Scatter(x=[portfolio_stats(optimal_sharpe_weights)['volatility']],
                         y=[portfolio_stats(optimal_sharpe_weights)['return']],
                         mode='markers',
                                   marker=dict(
        size=15,
        color='red',
        symbol='triangle-up',
        showscale=True)))

fig.add_trace(go.Scatter(x=[portfolio_stats(optimal_variance_weights)['volatility']],
                         y=[portfolio_stats(optimal_variance_weights)['return']],
                         mode='markers',
                                   marker=dict(
        size=15,
        color='green',
        symbol='triangle-up',
        showscale=True)))

fig.show()

## Second run --> exclude Kikkoman since the ESG ratings are bad
## Third run --> exclude NESTLE since esg are low

In [49]:
#ticker_list.remove('KIKOY')
#ticker_list.remove('NESN.SW')
data = fetch_data(ticker_list, verbose=False)
stocks = get_pandas_df(data)
num_assets = len(ticker_list)
adj_closes = stocks_df[[x for x in stocks.columns if x !='timestamp']]
returns = np.log(adj_closes / adj_closes.shift(1))

In [50]:
constraints = ({'type' : 'eq', 'fun': lambda x: np.sum(x) -1})
bounds = tuple((0,1) for x in range(num_assets))
initializer = num_assets * [1./num_assets,]

In [51]:
optimal_sharpe = optimize.minimize(minimize_sharpe,
                                  initializer,
                                  method = 'SLSQP',
                                  bounds = bounds,
                                  constraints = constraints)
print(optimal_sharpe)

     fun: -0.738221898610945
     jac: array([ 2.58393586e-04,  1.47356711e+00,  5.86584210e-05,  1.32399589e-01,
       -1.17003918e-04,  4.09910187e-01,  9.84015912e-02, -8.22991133e-05,
        3.50429580e-01,  1.36965945e-01,  2.14253981e+00,  3.97729084e-01,
        4.63841833e-01,  6.17519818e-01,  7.88870752e-01,  5.92847086e-01,
        1.71986572e-01])
 message: 'Optimization terminated successfully'
    nfev: 108
     nit: 6
    njev: 6
  status: 0
 success: True
       x: array([2.60494978e-01, 2.84575965e-16, 2.79970556e-02, 0.00000000e+00,
       2.99205654e-01, 2.94686150e-16, 0.00000000e+00, 4.12302313e-01,
       9.37021728e-17, 1.21430643e-17, 1.07785959e-15, 5.42372137e-17,
       2.06377884e-16, 1.25848767e-16, 1.12160715e-16, 0.00000000e+00,
       9.60603125e-17])


In [55]:
optimal_sharpe_weights=optimal_sharpe['x'].round(4)
list(zip(ticker_list,list(optimal_sharpe_weights)))

[('BARN.SW', 0.2605),
 ('E5H.SI', 0.0),
 ('BN.VI', 0.028),
 ('UN', 0.0),
 ('LISN.SW', 0.2992),
 ('SJM', 0.0),
 ('MDLZ', 0.0),
 ('HRL', 0.4123),
 ('GIS', 0.0),
 ('HSY', 0.0),
 ('WHG', 0.0),
 ('ADM', 0.0),
 ('K', 0.0),
 ('TATE.L', 0.0),
 ('BG', 0.0),
 ('ABF.L', 0.0),
 ('CAG', 0.0)]

The exact number are: - in round 4 are just more rounded

In [58]:
list(zip(ticker_list,list(optimal_sharpe['x']*100)))

[('BARN.SW', 26.049497763727704),
 ('E5H.SI', 2.845759652231328e-14),
 ('BN.VI', 2.7997055565635147),
 ('UN', 0.0),
 ('LISN.SW', 29.920565421380196),
 ('SJM', 2.946861504815601e-14),
 ('MDLZ', 0.0),
 ('HRL', 41.230231258328416),
 ('GIS', 9.370217275705972e-15),
 ('HSY', 1.214306433183765e-15),
 ('WHG', 1.0778595897764642e-13),
 ('ADM', 5.423721367858736e-15),
 ('K', 2.0637788353261577e-14),
 ('TATE.L', 1.2584876717125493e-14),
 ('BG', 1.1216071474362543e-14),
 ('ABF.L', 0.0),
 ('CAG', 9.60603124822157e-15)]